# 1. Import data

In [1]:
import pandas as pd
import numpy as np
from pyomo.common.timing import report_timing
import pyomo.environ as pyo
from pyomo.environ import *
from pyomo.opt import SolverFactory
from pyomo.opt import SolverStatus, TerminationCondition

In [2]:
data = pd.read_excel('data.xlsx')

In [3]:
data

index NETWORK FLT_TYPE    AREA COUNTRY   ROUTE   SEC2W  \
0     DADHANVN154A3211     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
1     DADHANVN154A3212     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
2     DADHANVN154A3213     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
3     DADHANVN154A3214     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
4     DADHANVN154A3215     DOM      PXR  HANDAD      VN  HANDAD  HANDAD   
...                ...     ...      ...     ...     ...     ...     ...   
5210  SYDSGNVN772B7873     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
5211  SYDSGNVN772B7874     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
5212  SYDSGNVN772B7875     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
5213  SYDSGNVN772B7876     INT      PXR     SWP      AU  SGNSYD  SGNSYD   
5214  SYDSGNVN772B7877     INT      PXR     SWP      AU  SGNSYD  SGNSYD   

      Sector from   to flight  DOW_ETD  DOW_ETA        ETD        ETA    AC  \
0     DADHAN  DAD  HAN  VN154        1        2  23.000000   0.333333  A321   
1     DADHAN  DAD  HAN  VN154        2        3  23.000000   0.333333  A321   
2     DADHAN  DAD  HAN  VN154        3        4  23.000000   0.333333  A321   
3     DADHAN  DAD  HAN  VN154        4        5  23.000000   0.333333  A321   
4     DADHAN  DAD  HAN  VN154        5        6  23.000000   0.333333  A321   
...      ...  ...  ...    ...      ...      ...        ...        ...   ...   
5210  SYDSGN  SYD  SGN  VN772        3        3   0.250000   9.166667  B787   
5211  SYDSGN  SYD  SGN  VN772        4        4   0.250000   9.333333  B787   
5212  SYDSGN  SYD  SGN  VN772        5        5   0.250000   9.333333  B787   
5213  SYDSGN  SYD  SGN  VN772        6        6   0.250000   9.333333  B787   
5214  SYDSGN  SYD  SGN  VN772        7        7   2.166667  11.250000  B787   

          revenue         cost  
0      236.346889   201.944430  
1      236.346889   201.944430  
2      236.346889   201.944430  
3      236.346889   201.944430  
4      236.346889   201.944430  
...           ...          ...  
5210  2174.084466  2175.806312  
5211  2174.084466  2175.806312  
5212  2174.084466  2175.806312  
5213  2174.084466  2175.806312  
5214  2174.084466  2175.806312  

[5215 rows x 18 columns]

In [4]:
# tạo dictionary về số tàu bay đã thuê mua:
fleet = {'B787':17,'A350':14,'A321':56}
#fleet = {'AT7':3,'RJ':1}

# 2. Sets

In [5]:
model = pyo.ConcreteModel()

In [6]:
report_timing()

<StreamHandler stdout (NOTSET)>

In [7]:
# create set of sector
# note: lam the nao de biet chuyen chieu di nao tuong ung voi chuyen chieu ve? co can tuong ung ko?
model.sector = pyo.Set(initialize = data['Sector'].unique())
sector = model.sector

           0 seconds to construct Set sector; 1 index total


In [8]:
# create set of aircraft type
model.ac_type = pyo.Set(initialize = data['AC'].unique())
ac_type = model.ac_type

           0 seconds to construct Set ac_type; 1 index total


In [9]:
# create set of flight no
model.flight_no = pyo.Set(initialize = data['flight'].unique())
flight_no = model.flight_no

           0 seconds to construct Set flight_no; 1 index total


In [10]:
# create set of DOW
model.DOW = pyo.Set(initialize = range(1,8), domain = PositiveIntegers)
DOW = model.DOW

           0 seconds to construct Set DOW; 1 index total


In [11]:
# create set of hour
model.hour = pyo.Set(initialize = range(0,24), domain = NonNegativeIntegers)
hour = model.hour

           0 seconds to construct Set hour; 1 index total


In [12]:
# create set of airport
airport_from = data['from'].unique()
airport_to = data['to'].unique()
airport_set = set(np.concatenate((airport_from,airport_to)))
model.airport = pyo.Set(initialize = airport_set, ordered = False)
airport = model.airport

           0 seconds to construct Set airport; 1 index total


In [13]:
# Tạo 1 set để làm index các chuyến bay: số hiệu + AC + DOW
model.flight_index = pyo.Set(initialize = data['index'])
flight_index = model.flight_index

    action taken
        0.01 seconds to construct Set flight_index; 1 index total


# 3. Parameters

# 4. Variables

In [14]:
model.assign_fleet = pyo.Var(flight_index, within = Binary, initialize = 1)
assign_fleet = model.assign_fleet

           0 seconds to construct Var assign_fleet; 5214 indices total


In [15]:
model.time_nodes = pyo.Var(airport, DOW, hour, ac_type, domain = NonNegativeIntegers)
time_nodes = model.time_nodes

           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
        0.05 seconds to construct Var time_nodes; 31752 indices total


# 5. Constraints

## 5.1. Balance constraints

Tại mỗi mốc thời gian, số tàu đậu đỗ theo từng loại tàu của mỗi mốc thời gian + số tàu bay hạ cánh phải tương đương với số tàu đậu đỗ của mốc thời gian kế tiếp + số tàu bay cất cánh (Node1 + inwards = Node2 + outwards). Ngoài ra, để đảm bảo giả định sản phẩm tần suất các tuần giống nhau, time node cuối cùng trong tuần (23h Chủ Nhật) phải balance với node đầu tiên trong tuần (0h Thứ Hai).

In [16]:
def balance_constraint(model, a,d,h,ac):
    # khung giờ đầu tiên của thứ hai phải cân bằng với khung giờ cuối cùng của chủ nhật
    # (giả định sản phẩm tần suất của các tuần giống nhau)
    if h == 0 and d == 1:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,7,23,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == 7)
                    &(data['ETA'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == 7)
                    &(data['ETD'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    # khung giờ đầu tiên trong ngày = khung giờ cuối cùng ngày hôm trước:
    elif h == 0:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,d-1,23,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == d-1)
                    &(data['ETA'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == d-1)
                    &(data['ETD'].between(23,24,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    # balance constraint cho các khung giờ trong 1 ngày:
    else:
        expr = (time_nodes[a,d,h,ac] == 
                time_nodes[a,d,h-1,ac]
                +sum(assign_fleet[i] for i in data[
                    (data['to'] == a)
                    &(data['DOW_ETA'] == d)
                    &(data['ETA'].between(h-1,h,inclusive = 'left'))
                    &(data['AC'] == ac)]['index'])
                -sum(assign_fleet[i] for i in data[
                    (data['from'] == a)
                    &(data['DOW_ETD'] == d)
                    &(data['ETD'].between(h-1,h,inclusive = 'left'))
                    &(data['AC'] == ac)]['index']))
    return expr

In [17]:
model.balance_constraint = pyo.Constraint(airport, DOW, hour, ac_type, rule = balance_constraint)

           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
           0 seconds to construct Set SetProduct_FiniteSet; 1 index total
       45.10 seconds to construct Constraint balance_constraint; 31752 indices total


## 5.2. Coverage constraints

Mỗi 1 số hiệu chuyến bay nếu được lựa chọn khai thác thì chỉ được dùng duy nhất 1 loại tàu bay trong ngày. (Vd: VN087 không thể khai thác đồng thời 321 và 787 tại cùng 1 ngày).

In [18]:
def coverage_constraint(model, f,d):
    if data[(data['flight']==f)&(data['DOW_ETD']==d)].empty:
        expr = pyo.Constraint.Skip
    else:
        expr = sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['DOW_ETD']==d)]['index']) <= 1
    return expr
# Rieeng các đường xuyên Đông Dương thì sẽ có 2 chuyến bay có chung 1 số hiệu chuyến bay trong 1 ngày, vì vậy phải thêm elif

In [19]:
model.coverage_constraint = pyo.Constraint(flight_no, DOW, rule = coverage_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
        2.13 seconds to construct Constraint coverage_constraint; 3367 indices total


## 5.3. Fleet constraints

Tổng số tàu bay tại các sân bay trong từng khung giờ không được lớn hơn số tàu bay đã thuê mua.

In [20]:
def fleet_constraint(model, d,h,ac):
    return pyo.inequality(0,sum(time_nodes[a,d,h,ac] for a in airport),fleet[ac])
# có thể tính chi phí tàu bay cố định = sum(time_nodes[a,d,h,ac] for a in airport)*chi phí 1 tàu

In [21]:
model.fleet_constraint = pyo.Constraint(DOW, hour, ac_type, rule = fleet_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
        0.04 seconds to construct Constraint fleet_constraint; 504 indices total


## 5.4. Airport constraints

Một số đường bay chỉ dùng được tàu thân rộng, một số đường bay khác chỉ dùng được tàu AT7 do hạn chế về khoảng cách bay và cơ sở hạ tầng sân bay.

In [22]:
long_haul = ['CDG','DME','SVO','FRA','LHR','LAX','SFO','SYD','MEL']

In [23]:
def airport_constraint(model, i):
    return sum(assign_fleet[i] for i in data[(data['AC']=='A321')&(data['to'].isin(long_haul))]['index']) == 0

## 5.5. Product constraints

Để đảm bảo tính đồng nhất của sản phẩm, các chuyến bay trên 1 đường bay phải sử dụng loại tàu bay giống nhau giữa các ngày trong tuần.

In [24]:
def product_constraint(model,f,ac,d):
    operating_day = list(data[(data['flight']==f)&(data['AC']==ac)]['DOW_ETD'])
    if d not in operating_day:
        expr = pyo.Constraint.Skip
    elif d == operating_day[0]:
        expr = pyo.Constraint.Skip
    else:
        expr = (sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['AC']==ac)&(data['DOW_ETD']==d)]['index'])
                == sum(assign_fleet[i] for i in data[(data['flight']==f)&(data['AC']==ac)&(data['DOW_ETD']==operating_day[operating_day.index(d)-1])]['index']))
    return expr

In [25]:
model.product_constraint = pyo.Constraint(flight_no, ac_type, DOW, rule = product_constraint)

           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
           0 seconds to construct Set SetProduct_OrderedSet; 1 index total
       10.23 seconds to construct Constraint product_constraint; 10101 indices total


In [26]:
model.product_constraint.pprint()

product_constraint : Size=4238, Index=product_constraint_index, Active=True
    Key                   : Lower : Body                                                                                                                                                                                                  : Upper : Active
      ('VN10', 'A350', 5) :   0.0 :                                                                                                                                         assign_fleet[CDGSGNVN10A3505] - assign_fleet[CDGSGNVN10A3503] :   0.0 :   True
      ('VN10', 'A350', 7) :   0.0 :                                                                                                                                         assign_fleet[CDGSGNVN10A3507] - assign_fleet[CDGSGNVN10A3505] :   0.0 :   True
      ('VN10', 'B787', 5) :   0.0 :                                                                                                                                        

     ('VN269', 'A321', 4) :   0.0 :                                                                                                                                       assign_fleet[HANSGNVN269A3214] - assign_fleet[HANSGNVN269A3213] :   0.0 :   True
     ('VN269', 'A321', 5) :   0.0 :                                                                                                                                       assign_fleet[HANSGNVN269A3215] - assign_fleet[HANSGNVN269A3214] :   0.0 :   True
     ('VN269', 'A321', 6) :   0.0 :                                                                                                                                       assign_fleet[HANSGNVN269A3216] - assign_fleet[HANSGNVN269A3215] :   0.0 :   True
     ('VN269', 'A321', 7) :   0.0 :                                                                                                                                       assign_fleet[HANSGNVN269A3217] - assign_fleet[HANSGNVN269A3216] :   0.0 :   T

     ('VN530', 'A321', 3) :   0.0 :                                                                                                                                       assign_fleet[HANPVGVN530A3213] - assign_fleet[HANPVGVN530A3212] :   0.0 :   True
     ('VN530', 'A321', 4) :   0.0 :                                                                                                                                       assign_fleet[HANPVGVN530A3214] - assign_fleet[HANPVGVN530A3213] :   0.0 :   True
     ('VN530', 'A321', 5) :   0.0 :                                                                                                                                       assign_fleet[HANPVGVN530A3215] - assign_fleet[HANPVGVN530A3214] :   0.0 :   True
     ('VN530', 'A321', 6) :   0.0 :                                                                                                                                       assign_fleet[HANPVGVN530A3216] - assign_fleet[HANPVGVN530A3215] :   0.0 :   T

# 6. Objective function

In [27]:
model.obj = pyo.Objective(expr = (sum(assign_fleet[i]*data[data['index']==i]['revenue'].values[0] for i in flight_index)
                          -sum(assign_fleet[i]*data[data['index']==i]['cost'].values[0] for i in flight_index)), sense = pyo.maximize)

           0 seconds to construct Objective obj; 1 index total


In [28]:
solver = SolverFactory('cbc', executable = "E:\\Fleet Assignment Model\\coin\\cbc.exe")

In [29]:
results = solver.solve(model, tee=True)

Welcome to the CBC MILP Solver 
Version: 2.10.5 
Build Date: Nov 24 2021 

command line - E:\Fleet Assignment Model\coin\cbc.exe -printingOptions all -import C:\Users\ADMIN\AppData\Local\Temp\tmpfd0xnvf8.pyomo.lp -stat=1 -solve -solu C:\Users\ADMIN\AppData\Local\Temp\tmpfd0xnvf8.pyomo.soln (default strategy 1)
Option for printingOptions changed from normal to all
 CoinLpIO::readLp(): Maximization problem reformulated as minimization
Coin0009I Switching back to maximization to get correct duals etc
Presolve is modifying 1 integer bounds and re-presolving
Presolve 3084 (-36527) rows, 3300 (-33667) columns and 33312 (-117878) elements
Statistics for presolved model
Original problem has 36965 integers (5213 of which binary)
Presolved problem has 3300 integers (988 of which binary)
==== 2312 zero objective 272 different
==== absolute objective values 272 different
==== for integers 2312 zero objective 272 different
==== for integers absolute objective values 272 different
===== end objectiv

Cbc0010I After 6900 nodes, 2451 on tree, -109498.78 best solution, best possible -109653.74 (155.37 seconds)
Cbc0010I After 7000 nodes, 2501 on tree, -109498.78 best solution, best possible -109653.74 (157.23 seconds)
Cbc0010I After 7100 nodes, 2551 on tree, -109498.78 best solution, best possible -109653.74 (158.85 seconds)
Cbc0038I Full problem 3077 rows 3297 columns, reduced to 492 rows 299 columns
Cbc0010I After 7200 nodes, 2602 on tree, -109498.78 best solution, best possible -109653.74 (160.13 seconds)
Cbc0010I After 7300 nodes, 2655 on tree, -109498.78 best solution, best possible -109653.74 (161.47 seconds)
Cbc0010I After 7400 nodes, 2702 on tree, -109498.78 best solution, best possible -109653.74 (163.18 seconds)
Cbc0004I Integer solution of -109579.86 found after 522783 iterations and 7493 nodes (164.61 seconds)
Cbc0010I After 7500 nodes, 1207 on tree, -109579.86 best solution, best possible -109653.74 (164.79 seconds)
Cbc0010I After 7600 nodes, 1255 on tree, -109579.86 best 

Cbc0010I After 14100 nodes, 2830 on tree, -109579.86 best solution, best possible -109629.12 (278.47 seconds)
Cbc0010I After 14200 nodes, 2876 on tree, -109579.86 best solution, best possible -109628.97 (280.45 seconds)
Cbc0010I After 14300 nodes, 2926 on tree, -109579.86 best solution, best possible -109628.71 (281.74 seconds)
Cbc0038I Full problem 3077 rows 3297 columns, reduced to 655 rows 412 columns
Cbc0010I After 14400 nodes, 2976 on tree, -109579.86 best solution, best possible -109628.67 (283.47 seconds)
Cbc0010I After 14500 nodes, 3026 on tree, -109579.86 best solution, best possible -109628.54 (285.00 seconds)
Cbc0010I After 14600 nodes, 3076 on tree, -109579.86 best solution, best possible -109628.54 (286.21 seconds)
Cbc0010I After 14700 nodes, 3126 on tree, -109579.86 best solution, best possible -109628.45 (287.70 seconds)
Cbc0010I After 14800 nodes, 3176 on tree, -109579.86 best solution, best possible -109628.29 (289.45 seconds)
Cbc0010I After 14900 nodes, 3231 on tree, 

Cbc0010I After 25100 nodes, 7236 on tree, -109579.86 best solution, best possible -109622.79 (456.31 seconds)
Cbc0010I After 25200 nodes, 7274 on tree, -109579.86 best solution, best possible -109622.79 (457.54 seconds)
Cbc0038I Full problem 3077 rows 3297 columns, reduced to 635 rows 412 columns
Cbc0010I After 25300 nodes, 7271 on tree, -109579.86 best solution, best possible -109622.79 (459.50 seconds)
Cbc0010I After 25400 nodes, 7272 on tree, -109579.86 best solution, best possible -109622.79 (461.10 seconds)
Cbc0010I After 25500 nodes, 7266 on tree, -109579.86 best solution, best possible -109622.79 (462.75 seconds)
Cbc0010I After 25600 nodes, 7259 on tree, -109579.86 best solution, best possible -109622.79 (464.42 seconds)
Cbc0010I After 25700 nodes, 7265 on tree, -109579.86 best solution, best possible -109622.79 (466.06 seconds)
Cbc0010I After 25800 nodes, 7260 on tree, -109579.86 best solution, best possible -109622.79 (467.78 seconds)
Cbc0010I After 25900 nodes, 7254 on tree, 

Cbc0010I After 32400 nodes, 9877 on tree, -109579.86 best solution, best possible -109621.57 (565.75 seconds)
Cbc0010I After 32500 nodes, 9926 on tree, -109579.86 best solution, best possible -109621.55 (567.14 seconds)
Cbc0010I After 32600 nodes, 9977 on tree, -109579.86 best solution, best possible -109621.55 (568.09 seconds)
Cbc0010I After 32700 nodes, 10026 on tree, -109579.86 best solution, best possible -109621.52 (569.20 seconds)
Cbc0010I After 32800 nodes, 10075 on tree, -109579.86 best solution, best possible -109621.51 (570.78 seconds)
Cbc0010I After 32900 nodes, 10125 on tree, -109579.86 best solution, best possible -109621.43 (572.53 seconds)
Cbc0010I After 33000 nodes, 10176 on tree, -109579.86 best solution, best possible -109621.41 (574.53 seconds)
Cbc0010I After 33100 nodes, 10169 on tree, -109579.86 best solution, best possible -109621.41 (576.15 seconds)
Cbc0010I After 33200 nodes, 10176 on tree, -109579.86 best solution, best possible -109621.41 (577.81 seconds)
Cbc0

Cbc0010I After 43100 nodes, 8444 on tree, -109600.53 best solution, best possible -109620.68 (762.60 seconds)
Cbc0038I Full problem 3077 rows 3297 columns, reduced to 552 rows 376 columns
Cbc0010I After 43200 nodes, 8487 on tree, -109600.53 best solution, best possible -109620.64 (764.61 seconds)
Cbc0010I After 43300 nodes, 8524 on tree, -109600.53 best solution, best possible -109620.6 (766.62 seconds)
Cbc0010I After 43400 nodes, 8568 on tree, -109600.53 best solution, best possible -109620.55 (768.61 seconds)
Cbc0010I After 43500 nodes, 8596 on tree, -109600.53 best solution, best possible -109620.49 (770.71 seconds)
Cbc0010I After 43600 nodes, 8634 on tree, -109600.53 best solution, best possible -109620.47 (772.66 seconds)
Cbc0010I After 43700 nodes, 8654 on tree, -109600.53 best solution, best possible -109620.46 (774.21 seconds)
Cbc0010I After 43800 nodes, 8690 on tree, -109600.53 best solution, best possible -109620.41 (775.88 seconds)
Cbc0010I After 43900 nodes, 8719 on tree, -

Cbc0038I Full problem 3077 rows 3297 columns, reduced to 610 rows 396 columns
Cbc0010I After 50400 nodes, 4077 on tree, -109612.35 best solution, best possible -109618.39 (897.54 seconds)
Cbc0010I After 50500 nodes, 4047 on tree, -109612.35 best solution, best possible -109618.31 (899.95 seconds)
Cbc0010I After 50600 nodes, 4021 on tree, -109612.35 best solution, best possible -109618.26 (902.02 seconds)
Cbc0010I After 50700 nodes, 3997 on tree, -109612.35 best solution, best possible -109618.23 (904.32 seconds)
Cbc0010I After 50800 nodes, 3963 on tree, -109612.35 best solution, best possible -109618.2 (905.89 seconds)
Cbc0010I After 50900 nodes, 3954 on tree, -109612.35 best solution, best possible -109618.17 (908.14 seconds)
Cbc0010I After 51000 nodes, 3963 on tree, -109612.35 best solution, best possible -109618.13 (910.47 seconds)
Cbc0010I After 51100 nodes, 3952 on tree, -109612.35 best solution, best possible -109618.09 (912.22 seconds)
Cbc0010I After 51200 nodes, 3925 on tree, -

Cbc0010I After 61400 nodes, 1008 on tree, -109612.35 best solution, best possible -109614.11 (1105.36 seconds)
Cbc0010I After 61500 nodes, 961 on tree, -109612.35 best solution, best possible -109614.11 (1107.02 seconds)
Cbc0010I After 61600 nodes, 913 on tree, -109612.35 best solution, best possible -109614.11 (1108.74 seconds)
Cbc0010I After 61700 nodes, 868 on tree, -109612.35 best solution, best possible -109614.11 (1110.39 seconds)
Cbc0010I After 61800 nodes, 822 on tree, -109612.35 best solution, best possible -109614.11 (1112.11 seconds)
Cbc0010I After 61900 nodes, 800 on tree, -109612.35 best solution, best possible -109614.11 (1113.31 seconds)
Cbc0010I After 62000 nodes, 756 on tree, -109612.35 best solution, best possible -109614.11 (1114.93 seconds)
Cbc0010I After 62100 nodes, 730 on tree, -109612.35 best solution, best possible -109614.03 (1116.58 seconds)
Cbc0010I After 62200 nodes, 683 on tree, -109612.35 best solution, best possible -109613.95 (1118.25 seconds)
Cbc0010I 

# 7. Results

In [30]:
model.pprint()

12 Set Declarations
    DOW : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain           : Size : Members
        None :     1 : PositiveIntegers :    7 : {1, 2, 3, 4, 5, 6, 7}
    ac_type : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    3 : {'A321', 'A350', 'B787'}
    airport : Size=1, Index=None, Ordered=False
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   63 : {'BKK', 'BMV', 'CAN', 'CDG', 'CGK', 'CGO', 'CJU', 'CTU', 'CXR', 'CZX', 'DAD', 'DLI', 'DME', 'FRA', 'FUK', 'HAN', 'HET', 'HGH', 'HKG', 'HND', 'HPH', 'HRB', 'HUI', 'ICN', 'JJN', 'KHH', 'KIX', 'KMG', 'KUL', 'LHR', 'LPQ', 'MEL', 'MWX', 'NGO', 'NKG', 'NNG', 'NRT', 'PEK', 'PNH', 'PQC', 'PUS', 'PVG', 'PXU', 'REP', 'RGN', 'SGN', 'SHE', 'SIN', 'SYD', 'TBB', 'TEN', 'THD', 'TPE', 'TSN', 'UIH', 'VCA', 'VCL', 'VDH', 'VDO', 'VII', 'VTE', 'YIH', 'YNT'}
    balance_constraint_index : Size=1, Index=None, Ordered=False


         HANSGNVN239A3213 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239A3214 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239A3215 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239A3216 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239A3217 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239A3501 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3502 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3503 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3504 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3505 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3506 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239A3507 :     0 :   1.0 :     1 : False : False : Binary
         HANSGNVN239B7871 :     0 :   0.0 :     1 : False : False : Binary
         HANSGNVN239B7872

        Key                    : Lower : Value : Upper : Fixed : Stale : Domain
         ('BKK', 1, 0, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 0, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 0, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 1, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 1, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 1, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 2, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 2, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 2, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('BKK', 1, 3, 'A321') :     0 :   0.0 :  None : False : False : NonNegativ

         ('CTU', 3, 7, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 7, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 8, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 8, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 8, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 9, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 9, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
         ('CTU', 3, 9, 'B787') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
        ('CTU', 3, 10, 'A321') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
        ('CTU', 3, 10, 'A350') :     0 :   0.0 :  None : False : False : NonNegativeIntegers
        ('CTU', 3, 10, 'B787') :     0 :   0.0 :  None : False : False

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




         ('RGN', 3, 1, 'A321') :   0.0 :                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   time_nodes[RGN,3,1,A321] - time_nodes[RGN,3,0,A321] :   0.0 :   True
         ('RGN', 3, 1, 'A350') :   0.0 :                                                                                                                                                                                                               

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



        Key           : Lower : Body                                                                                                : Upper : Active
          ('VN10', 3) :  -Inf :                                       assign_fleet[CDGSGNVN10A3503] + assign_fleet[CDGSGNVN10B7873] :   1.0 :   True
          ('VN10', 5) :  -Inf :                                       assign_fleet[CDGSGNVN10A3505] + assign_fleet[CDGSGNVN10B7875] :   1.0 :   True
          ('VN10', 7) :  -Inf :                                       assign_fleet[CDGSGNVN10A3507] + assign_fleet[CDGSGNVN10B7877] :   1.0 :   True
         ('VN105', 1) :  -Inf :    assign_fleet[DADSGNVN105A3211] + assign_fleet[DADSGNVN105A3501] + assign_fleet[DADSGNVN105B7871] :   1.0 :   True
         ('VN105', 2) :  -Inf :    assign_fleet[DADSGNVN105A3212] + assign_fleet[DADSGNVN105A3502] + assign_fleet[DADSGNVN105B7872] :   1.0 :   True
         ('VN105', 3) :  -Inf :    assign_fleet[DADSGNVN105A3213] + assign_fleet[DADSGNVN105A3503] + assig

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [31]:
results.solver.status

<SolverStatus.ok: 'ok'>

In [32]:
results.solver.termination_condition

<TerminationCondition.optimal: 'optimal'>

In [33]:
optimal_values = [value(assign_fleet[i]) for i in assign_fleet]

In [40]:
df_time_nodes = pd.DataFrame.from_dict(time_nodes.extract_values(), orient="index", columns=["variable value"])
df_time_nodes.reset_index(inplace = True)
print(df_time_nodes)

                    index  variable value
0       (FRA, 1, 0, A321)             0.0
1       (FRA, 1, 0, A350)             0.0
2       (FRA, 1, 0, B787)             0.0
3       (FRA, 1, 1, A321)             0.0
4       (FRA, 1, 1, A350)             0.0
...                   ...             ...
31747  (HND, 7, 22, A350)             0.0
31748  (HND, 7, 22, B787)             0.0
31749  (HND, 7, 23, A321)             0.0
31750  (HND, 7, 23, A350)             0.0
31751  (HND, 7, 23, B787)             0.0

[31752 rows x 2 columns]


In [41]:
df_time_nodes.to_excel('time_nodes.xlsx')

In [35]:
df_assign_fleet = pd.DataFrame.from_dict(assign_fleet.extract_values(), orient='index', columns=[str(assign_fleet)])
df_assign_fleet.reset_index(inplace = True)
print(df_assign_fleet)

                 index  assign_fleet
0     DADHANVN154A3211           0.0
1     DADHANVN154A3212           0.0
2     DADHANVN154A3213           0.0
3     DADHANVN154A3214           0.0
4     DADHANVN154A3215           0.0
...                ...           ...
5209  SYDSGNVN772B7873           0.0
5210  SYDSGNVN772B7874           0.0
5211  SYDSGNVN772B7875           0.0
5212  SYDSGNVN772B7876           0.0
5213  SYDSGNVN772B7877           0.0

[5214 rows x 2 columns]


In [36]:
result = data.merge(df_assign_fleet, on = 'index')

In [37]:
result.to_excel('result.xlsx')